In [2]:
# To ignore unimporant system warnings
import warnings
warnings.filterwarnings("ignore")

# We will use Pandas, Numpy, and Matplotlib which is a package for visualization with Python
import pandas as pd
#pd.set_option('display.max_rows',1000)
import numpy as np
import geopandas as gpd
from datetime import datetime
from geodatasets import get_path

# This is a library for accessing and parsing data through URLs
import urllib.request, json 
import urllib.parse
from urllib.parse import urlencode

# Using folium to create a map
import folium
from folium import plugins
import matplotlib.pyplot as plt
import seaborn as sns # visualization styling package
import branca  # For color gradient
%matplotlib inline 

In [54]:
routes = pd.read_csv("./GTFS B/routes.txt")
shapes = pd.read_csv("./GTFS B/shapes.txt")
shapes1 = shapes[shapes['shape_id'].str.startswith('B10026')] 
shapes2 = shapes[shapes['shape_id'].str.startswith('B20')] 
shapes

shape_id  shape_pt_lat  shape_pt_lon  shape_pt_sequence
0          B10025     40.578199    -73.939761              10001
1          B10025     40.578252    -73.939799              10002
2          B10025     40.578352    -73.939819              10003
3          B10025     40.578329    -73.940025              10004
4          B10025     40.578329    -73.940025              20001
...           ...           ...           ...                ...
103719  SBS821520     40.644112    -73.877609             220015
103720  SBS821520     40.644022    -73.877519             220016
103721  SBS821520     40.643452    -73.877919             220017
103722  SBS821520     40.643061    -73.878185             220018
103723  SBS821520     40.642962    -73.878253             220019

[103724 rows x 4 columns]

In [58]:

# Convert shape_pt_sequence to numeric to ensure correct ordering
shapes['shape_pt_sequence'] = pd.to_numeric(shapes['shape_pt_sequence'])

# Sort data to ensure points are in correct order
shapes = shapes.sort_values(by=['shape_id', 'shape_pt_sequence'])

# Group by shape_id and create LineString geometry
lines = shapes.groupby('shape_id').apply(
    lambda x: LineString(x[['shape_pt_lon', 'shape_pt_lat']].values)
).reset_index(name='geometry')

# Convert to GeoDataFrame
gdf = gpd.GeoDataFrame(lines, geometry='geometry', crs="EPSG:4326")  # WGS 84 CRS
gdf


shape_id                                           geometry
0     B10025  LINESTRING (-73.93976 40.5782, -73.9398 40.578...
1     B10026  LINESTRING (-73.93976 40.5782, -73.9398 40.578...
2     B10052  LINESTRING (-74.02854 40.62189, -74.02869 40.6...
3     B10053  LINESTRING (-73.94002 40.57833, -73.94072 40.5...
4     B10054  LINESTRING (-73.98531 40.59678, -73.98528 40.5...
..       ...                                                ...
424  X370022  LINESTRING (-73.97285 40.76249, -73.97376 40.7...
425  X380025  LINESTRING (-73.98636 40.58334, -73.98637 40.5...
426  X380026  LINESTRING (-74.00266 40.57376, -74.00281 40.5...
427  X380027  LINESTRING (-73.97285 40.76249, -73.97376 40.7...
428  X380028  LINESTRING (-73.97285 40.76249, -73.97376 40.7...

[429 rows x 2 columns]

In [57]:

# Calculate map center (mean of all points)
center_lat = gdf.geometry.centroid.y.mean()
center_lon = gdf.geometry.centroid.x.mean()

# Create a folium map centered at the calculated location
m = folium.Map(location=[center_lat, center_lon], zoom_start=13)

# Add each route as a line
for _, row in gdf.iterrows():
    folium.PolyLine(
        locations=[(lat, lon) for lon, lat in row.geometry.coords],  # Extract coordinates correctly
        color="blue",  # You can assign unique colors if needed
        weight=3,
        opacity=0.8,
        popup=f"Shape ID: {row['shape_id']}"  # Display shape_id on click
    ).add_to(m)

# Display the map
m



In [45]:
import pandas as pd
import geopandas as gpd
import folium

# Calculate map center
center_lat = shapes2['shape_pt_lat'].mean()
center_lon = shapes2['shape_pt_lon'].mean()
m = folium.Map(location=[center_lat, center_lon], zoom_start=13)

# Add individual points with popups
for idx, row in shapes2.iterrows():
    folium.CircleMarker(
        location=[row['shape_pt_lat'], row['shape_pt_lon']],
        radius=3,  # Size of the point
        color='blue',
        fill=True,
        fill_color='blue',
        fill_opacity=0.8,
        popup=f"Shape ID: {row['shape_id']}"  # Popup with shape_id
    ).add_to(m)

# Display the map
m


In [51]:
shapes_routes = pd.read_csv("./GTFS B/shapes.txt")
unique_shape_ids = shapes_routes[shapes_routes['shape_id'].str.startswith('B20')]['shape_id'].unique()
unique_shape_ids_list = unique_shape_ids.tolist()
unique_shape_ids_list


['B20010', 'B20012', 'B200030', 'B200033', 'B200034', 'B200039', 'B200114']

In [53]:
import pandas as pd
import geopandas as gpd
import folium
import matplotlib.pyplot as plt

# Generate distinct colors for each unique shape_id
unique_shape_ids = shapes2['shape_id'].unique()
color_map = {shape_id: plt.cm.get_cmap('tab10')(i) for i, shape_id in enumerate(unique_shape_ids)}

# Convert colors to hex format
color_map = {k: "#{:02x}{:02x}{:02x}".format(
    int(v[0] * 255), int(v[1] * 255), int(v[2] * 255)) for k, v in color_map.items()}

# Calculate map center
center_lat = shapes2['shape_pt_lat'].mean()
center_lon = shapes2['shape_pt_lon'].mean()
m = folium.Map(location=[center_lat, center_lon], zoom_start=13)

# Add lines for each shape_id
for shape_id in unique_shape_ids:
    shape_data = shapes2[shapes2['shape_id'] == shape_id]
    
    folium.PolyLine(
        locations=shape_data[['shape_pt_lat', 'shape_pt_lon']].values,
        color=color_map[shape_id],
        weight=3,
        opacity=0.8,
        popup=f"Shape ID: {shape_id}"
    ).add_to(m)

# Display the map
m
